In [82]:
import pandas as pd 
from umap import UMAP
from hdbscan import HDBSCAN
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import CountVectorizer
 
from bertopic import BERTopic
from bertopic.representation import KeyBERTInspired
from bertopic.vectorizers import ClassTfidfTransformer

from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
import nltk
from nltk.corpus import wordnet

nltk.download('wordnet')
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package wordnet to /home/ehmindev/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /home/ehmindev/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/ehmindev/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [83]:
df = pd.read_excel("savedrecs.xls")

print(df)

    Publication Type                                            Authors   
0                  C  Deng, J; Dong, W; Socher, R; Li, LJ; Li, K; Li...  \
1                  J  Russakovsky, O; Deng, J; Su, H; Krause, J; Sat...   
2                  C  Szegedy, C; Vanhoucke, V; Ioffe, S; Shlens, J;...   
3                  C            Wang, XL; Girshick, R; Gupta, A; He, KM   
4                  C  Liu, Z; Lin, YT; Cao, Y; Hu, H; Wei, YX; Zhang...   
..               ...                                                ...   
995                J  Aimar, A; Mostafa, H; Calabrese, E; Rios-Navar...   
996                J                 Gong, K; Catana, C; Qi, JY; Li, QZ   
997                J         Hoskere, V; Park, JW; Yoon, H; Spencer, BF   
998                J  Sharif, M; Khan, MA; Zahid, F; Shah, JH; Akram, T   
999                J  Jegham, I; Ben Khalifa, A; Alouani, I; Mahjoub...   

     Book Authors Book Editors Book Group Authors   
0             NaN          NaN               I

In [84]:
df = df[["Article Title","Abstract"]]

In [85]:
docs = df["Abstract"].astype(str).tolist()
docs

['The explosion of image data on the Internet has the potential to foster more sophisticated and robust models and algorithms to index, retrieve, organize and interact with images and multimedia data. But exactly how such data can be harnessed and organized remains a critical problem. We introduce here a new database called ImageNet, a large-scale ontology of images built upon the backbone of the WordNet structure. ImageNet aims to populate the majority of the 80,000 synsets of WordNet with an average of 5001000 clean and full resolution images. This will result in tens of millions of annotated images organized by the semantic hierarchy of WordNet. This paper offers a detailed analysis of ImageNet in its current state: 12 subtrees with 5247 synsets and 3.2 million images in total. We show that ImageNet is much larger in scale and diversity and much more accurate than the current image datasets. Constructing such a large-scale database is a challenging task. We describe the data collect

In [86]:
def get_wordnet_pos(treebank_tag):
    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return None

## Test POS Tagging Effect

In [87]:
lemmatizer = WordNetLemmatizer()
a = docs[0].split(" ")

print(a)
print([lemmatizer.lemmatize(word) for word in a])
tokens = word_tokenize(docs[0])
print([lemmatizer.lemmatize(word[0],pos = get_wordnet_pos(word[1])) if get_wordnet_pos(word[1]) else word[0]  for word in nltk.pos_tag(tokens)])

['The', 'explosion', 'of', 'image', 'data', 'on', 'the', 'Internet', 'has', 'the', 'potential', 'to', 'foster', 'more', 'sophisticated', 'and', 'robust', 'models', 'and', 'algorithms', 'to', 'index,', 'retrieve,', 'organize', 'and', 'interact', 'with', 'images', 'and', 'multimedia', 'data.', 'But', 'exactly', 'how', 'such', 'data', 'can', 'be', 'harnessed', 'and', 'organized', 'remains', 'a', 'critical', 'problem.', 'We', 'introduce', 'here', 'a', 'new', 'database', 'called', 'ImageNet,', 'a', 'large-scale', 'ontology', 'of', 'images', 'built', 'upon', 'the', 'backbone', 'of', 'the', 'WordNet', 'structure.', 'ImageNet', 'aims', 'to', 'populate', 'the', 'majority', 'of', 'the', '80,000', 'synsets', 'of', 'WordNet', 'with', 'an', 'average', 'of', '5001000', 'clean', 'and', 'full', 'resolution', 'images.', 'This', 'will', 'result', 'in', 'tens', 'of', 'millions', 'of', 'annotated', 'images', 'organized', 'by', 'the', 'semantic', 'hierarchy', 'of', 'WordNet.', 'This', 'paper', 'offers', 'a

In [88]:
lemmatizer = WordNetLemmatizer()

for i in range(len(docs)):
    tokens = word_tokenize(docs[i])
    docs[i] = " ".join([lemmatizer.lemmatize(word[0],pos = get_wordnet_pos(word[1])) if get_wordnet_pos(word[1]) else word[0]  for word in nltk.pos_tag(tokens)])

In [89]:
docs

['The explosion of image data on the Internet have the potential to foster more sophisticated and robust model and algorithm to index , retrieve , organize and interact with image and multimedia data . But exactly how such data can be harness and organize remain a critical problem . We introduce here a new database call ImageNet , a large-scale ontology of image build upon the backbone of the WordNet structure . ImageNet aim to populate the majority of the 80,000 synset of WordNet with an average of 5001000 clean and full resolution image . This will result in ten of million of annotated image organize by the semantic hierarchy of WordNet . This paper offer a detailed analysis of ImageNet in its current state : 12 subtrees with 5247 synset and 3.2 million image in total . We show that ImageNet be much large in scale and diversity and much more accurate than the current image datasets . Constructing such a large-scale database be a challenging task . We describe the data collection sche

In [91]:
embedding_model = SentenceTransformer("all-MiniLM-L6-v2")
umap_model = UMAP(n_neighbors=15, n_components=5, min_dist=0.0, metric='cosine')
hdbscan_model = HDBSCAN(min_cluster_size=15, metric='euclidean', cluster_selection_method='eom', prediction_data=True)
vectorizer_model = CountVectorizer(stop_words="english")
ctfidf_model = ClassTfidfTransformer()

In [92]:
model = BERTopic(
  embedding_model=embedding_model,        
  umap_model=umap_model,               
  hdbscan_model=hdbscan_model,              
  vectorizer_model=vectorizer_model, 
  ctfidf_model=ctfidf_model,
  nr_topics=50,
  n_gram_range=(1,2)       
)


In [93]:
topics, probabilities = model.fit_transform(docs)

In [94]:
topic_df = model.get_topic_info()
topic_df

Topic  Count                                    Name
0      -1    294        -1_vision_image_computer_network
1       0     28         0_tracking_tracker_track_object
2       1     45              1_plant_fruit_disease_crop
3       2     49    2_face_facial_expression_recognition
4       3    104    3_crack_structural_defect_inspection
5       4     39     4_action_human_recognition_activity
6       5     22          5_id_pedestrian_vehicle_person
7       6     68              6_image_rain_method_sparse
8       7     73                  7_3d_point_shape_depth
9       8     22                 8_iot_reality_mobile_vr
10      9     30           9_accelerator_cnn_fpga_design
11     10     33             10_word_text_image_sentence
12     11     17          11_domain_gan_adaptation_image
13     12     63  12_image_segmentation_medical_clinical
14     13     19  13_remote_deep_classification_building
15     14     24     14_saliency_attention_salient_model
16     15     18           15_object_detection_small_sod
17     16     25                16_deep_learning_data_dl
18     17     27            17_network_transfer_bn_batch

In [95]:
get_topic = model.get_topic
get_topic(1)

[('plant', 0.05521268060786522),
 ('fruit', 0.04718308867860821),
 ('disease', 0.034983193663603765),
 ('crop', 0.03471293904277741),
 ('leaf', 0.03219516429158114),
 ('image', 0.028481900080512393),
 ('specie', 0.025927136116777667),
 ('identification', 0.024594602284865617),
 ('food', 0.023352638343164013),
 ('use', 0.02323990628169537)]

In [96]:
zero=[]
number=[]
for i in range(len(topic_df)):
  zero.append('0')
  number.append(i-1)

topic_word_df=pd.DataFrame({
    'topic_num':number,
    'topic':topic_df['Name'],
    'w1':zero,
    'w2':zero,
    'w3':zero,
    'w4':zero,
    'w5':zero,
    'w6':zero,
    'w7':zero,
    'w8':zero,
    'w9':zero,
    'w10':zero
})

# 각 토픽별 10개 단어 정리
col = topic_word_df.columns
for i in range(len(topic_word_df)):
  for j in range(10):
    topic_word_df[col[j+2]][i]=get_topic(i-1)[j][0]

In [97]:
topic_word_df

topic_num                                   topic           w1   
0          -1        -1_vision_image_computer_network       vision  \
1           0         0_tracking_tracker_track_object     tracking   
2           1              1_plant_fruit_disease_crop        plant   
3           2    2_face_facial_expression_recognition         face   
4           3    3_crack_structural_defect_inspection        crack   
5           4     4_action_human_recognition_activity       action   
6           5          5_id_pedestrian_vehicle_person           id   
7           6              6_image_rain_method_sparse        image   
8           7                  7_3d_point_shape_depth           3d   
9           8                 8_iot_reality_mobile_vr          iot   
10          9           9_accelerator_cnn_fpga_design  accelerator   
11         10             10_word_text_image_sentence         word   
12         11          11_domain_gan_adaptation_image       domain   
13         12  12_image_segmentation_medical_clinical        image   
14         13  13_remote_deep_classification_building       remote   
15         14     14_saliency_attention_salient_model     saliency   
16         15           15_object_detection_small_sod       object   
17         16                16_deep_learning_data_dl         deep   
18         17            17_network_transfer_bn_batch      network   

              w2              w3           w4           w5           w6   
0          image        computer      network     learning       object  \
1        tracker           track       object       target       visual   
2          fruit         disease         crop         leaf        image   
3         facial      expression  recognition     database          age   
4     structural          defect   inspection          use    detection   
5          human     recognition     activity        video       motion   
6     pedestrian         vehicle       person        crowd        world   
7           rain          method       sparse     function       matrix   
8          point           shape        depth        scene       method   
9        reality          mobile           vr  application   technology   
10           cnn            fpga       design       energy        layer   
11          text           image     sentence     language        model   
12           gan      adaptation        image  adversarial         gans   
13  segmentation         medical     clinical         deep     learning   
14          deep  classification     building      imagery         data   
15     attention         salient        model          map    detection   
16     detection           small          sod       aerial     detector   
17      learning            data           dl      network  application   
18      transfer              bn        batch        model         task   

            w7              w8              w9          w10  
0         deep             use           model       method  
1       online          filter     correlation   appearance  
2       specie  identification            food          use  
3        image           model        computer      emotion  
4        based          method      monitoring       vision  
5     temporal          method           based     research  
6      feature            open  identification    detection  
7      propose       algorithm          streak      problem  
8         data       algorithm           cloud        image  
9   blockchain           smart       augmented          iov  
10    hardware             dnn     computation      network  
11        task          visual         natural  description  
12       learn          method      generative      cartoon  
13         use          method       diagnosis      network  
14        land   hyperspectral       satellite     learning  
15     propose         feature          object       visual  
16    learning            deep          yolov3  

In [98]:
model.get_document_info(docs)

Document  Topic   
0    The explosion of image data on the Internet ha...     10  \
1    The ImageNet Large Scale Visual Recognition Ch...     -1   
2    Convolutional network be at the core of most s...     17   
3    Both convolutional and recurrent operation be ...     -1   
4    This paper present a new vision Transformer , ...     -1   
..                                                 ...    ...   
995  Convolutional neural network ( CNNs ) have bec...      9   
996  Recently , deep neural network have be widely ...     12   
997  Computer vision technique for extract dynamic ...      3   
998  Human action recognition from a video sequence...      4   
999  Within a large range of application in compute...      4   

                                       Name   
0               10_word_text_image_sentence  \
1          -1_vision_image_computer_network   
2              17_network_transfer_bn_batch   
3          -1_vision_image_computer_network   
4          -1_vision_image_computer_network   
..                                      ...   
995           9_accelerator_cnn_fpga_design   
996  12_image_segmentation_medical_clinical   
997    3_crack_structural_defect_inspection   
998     4_action_human_recognition_activity   
999     4_action_human_recognition_activity   

                                           Top_n_words  Probability   
0    word - text - image - sentence - language - mo...     0.474530  \
1    vision - image - computer - network - learning...     0.000000   
2    network - transfer - bn - batch - model - task...     0.848122   
3    vision - image - computer - network - learning...     0.000000   
4    vision - image - computer - network - learning...     0.000000   
..                                                 ...          ...   
995  accelerator - cnn - fpga - design - energy - l...     1.000000   
996  image - segmentation - medical - clinical - de...     0.850780   
997  crack - structural - defect - inspection - use...     1.000000   
998  action - human - recognition - activity - vide...     1.000000   
999  action - human - recognition - activity - vide...     1.000000   

     Representative_document  
0                      False  
1                      False  
2                      False  
3                      False  
4                      False  
..                       ...  
995                    False  
996                    False  
997                    False  
998                    False  
999                    False  

[1000 rows x 6 columns]

In [99]:
model.visualize_barchart()

In [100]:
model.visualize_heatmap()

In [101]:
model.visualize_topics()